In [16]:
from google.colab import files
uploaded = files.upload()

Saving accessibleRoutesMARTA.csv.zip to accessibleRoutesMARTA.csv.zip


In [17]:
import zipfile
import os

# Name of the zip file uploaded
zip_file = 'accessibleRoutesMARTA.csv.zip'

# Specify the directory where to extract files
extract_dir = '/content/unzipped_files'

# Unzipping the file
with zipfile.ZipFile(zip_file, 'r') as zip_ref:
    zip_ref.extractall(extract_dir)

# Check the contents of the unzipped file
os.listdir(extract_dir)


['accessibleRoutesMARTA.csv', '__MACOSX']

In [18]:
import pandas as pd

# Load the CSV file from the extracted folder
df = pd.read_csv('/content/unzipped_files/accessibleRoutesMARTA.csv')  # Replace with the actual extracted file name

<ipython-input-18-622d4e0af4ea>:4: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('/content/unzipped_files/accessibleRoutesMARTA.csv')  # Replace with the actual extracted file name


In [19]:
import pandas as pd
import ipywidgets as widgets
from datetime import datetime, timedelta

In [30]:
import ipywidgets as widgets
import folium
import pandas as pd
from ipywidgets import interactive
from IPython.display import display, HTML
from datetime import datetime

# Load your DataFrame (from the specified file path)
df = pd.read_csv('/content/unzipped_files/accessibleRoutesMARTA.csv')  # Adjust path as necessary

# Ensure that the route_short_name column is string to handle both numeric and text data
df['route_short_name'] = df['route_short_name'].astype(str)

# Create route_type dropdown widget (bus/train)
route_type_dropdown = widgets.Dropdown(
    options=['Bus', 'Train'],
    description='Route Type:',
)

# Create route selection dropdown widget
route_dropdown = widgets.Dropdown(
    options=[],  # Start with an empty list
    description='Route:',
)

# Create a time picker for the user to input arrival time (HH:MM format)
arrival_time_picker = widgets.Text(
    description='Arrival Time:',
    placeholder='Enter time in HH:MM format',
)

# Function to update route dropdown options based on the selected route type (Bus or Train)
def update_route_options(route_type):
    if route_type == 'Bus':
        # Bus routes are numeric (in string form)
        route_dropdown.options = [x for x in df['route_short_name'].unique() if x.isnumeric()]
    else:
        # Train routes are non-numeric (text-based)
        route_dropdown.options = [x for x in df['route_short_name'].unique() if x.isalpha()]

# Attach the function to update route options based on route type
route_type_dropdown.observe(lambda change: update_route_options(change.new), names='value')

# Function to filter and return accessible stops and calculate percentage
def filter_data(route_type, route_short_name):
    # Filter data based on route type (Bus or Train)
    if route_type == 'Bus':
        selected_routes = df[(df['route_short_name'] == route_short_name) & (df['route_short_name'].str.isnumeric())]
    else:
        selected_routes = df[(df['route_short_name'] == route_short_name) & (df['route_short_name'].str.isalpha())]

    # Get accessible and not accessible stops
    accessible_stops = selected_routes[selected_routes['accessibility_status'] == 'Accessible']
    not_accessible_stops = selected_routes[selected_routes['accessibility_status'] != 'Accessible']

    # Calculate accessibility percentage
    total_stops = len(selected_routes)
    accessible_stop_count = len(accessible_stops)
    accessibility_percentage = (accessible_stop_count / total_stops) * 100 if total_stops > 0 else 0

    return accessible_stops, not_accessible_stops, accessibility_percentage

# Function to generate the map based on selected route and type
def generate_map(route_type, route_short_name, arrival_time):
    # Convert arrival_time to datetime for comparison (HH:MM format)
    try:
        arrival_time = datetime.strptime(arrival_time, "%H:%M")
    except ValueError:
        print("Invalid time format. Please enter time in HH:MM format.")
        return

    # Filter the data to get accessible and not accessible stops and percentage
    accessible_stops, not_accessible_stops, accessibility_percentage = filter_data(route_type, route_short_name)

    if len(accessible_stops) > 0 or len(not_accessible_stops) > 0:
        # Map centered on the first accessible stop (or any available stop)
        start_lat = accessible_stops['stop_lat'].iloc[0] if len(accessible_stops) > 0 else not_accessible_stops['stop_lat'].iloc[0]
        start_lon = accessible_stops['stop_lon'].iloc[0] if len(accessible_stops) > 0 else not_accessible_stops['stop_lon'].iloc[0]
        m = folium.Map(location=[start_lat, start_lon], zoom_start=13)

        # Add markers for accessible stops (green)
        for _, stop in accessible_stops.iterrows():
            popup_content = f"Stop Name: {stop['stop_name']}<br>Accessibility Status: Accessible"
            folium.Marker(
                location=[stop['stop_lat'], stop['stop_lon']],
                popup=popup_content,
                icon=folium.Icon(color='green')
            ).add_to(m)

        # Add markers for not accessible stops (red)
        for _, stop in not_accessible_stops.iterrows():
            # Assuming we want to show the potential time window for accessibility status change
            not_accessible_time_window = "Accessible from 6:00 AM to 9:00 AM"  # Example, adjust based on your data

            popup_content = f"Stop Name: {stop['stop_name']}<br>Accessibility Status: Not Accessible<br>Potentially Accessible: {not_accessible_time_window}"
            folium.Marker(
                location=[stop['stop_lat'], stop['stop_lon']],
                popup=popup_content,
                icon=folium.Icon(color='red')
            ).add_to(m)

        # Add a marker for accessibility percentage (use a different color if necessary)
        folium.Marker(
            location=[start_lat, start_lon],
            popup=f"Accessibility: {accessibility_percentage:.2f}%",
            icon=folium.Icon(color='blue')
        ).add_to(m)

        # Display map directly in the notebook
        display(m)

        print(f"Accessibility Percentage: {accessibility_percentage:.2f}%")
        print(f"User Arrival Time: {arrival_time.strftime('%H:%M')}")
    else:
        print("No stops available for this route.")

# Initialize the route options
update_route_options(route_type_dropdown.value)

# Create an interactive plot with route selection
interactive_plot = interactive(generate_map,
                               route_type=route_type_dropdown,
                               route_short_name=route_dropdown,
                               arrival_time=arrival_time_picker)
output = interactive_plot.children[-1]
output.layout.height = '800px'
interactive_plot

<ipython-input-30-28db97034471>:9: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('/content/unzipped_files/accessibleRoutesMARTA.csv')  # Adjust path as necessary


interactive(children=(Dropdown(description='Route Type:', options=('Bus', 'Train'), value='Bus'), Dropdown(des…